# Numerical Solutions of the one and two-dimensional Time Dependent Schrodinger Equation

In this notebook we want to solve both the one-dimensional and the two-dimensional time-dependent Schrödinger equation.

$i\hbar\frac{\partial}{\partial t} \Psi(\mathbf{r},t) = \left [ \frac{-\hbar^2}{2m}\nabla^2 + V(\mathbf{r},t)\right ] \Psi(\mathbf{r},t)$

in which we take $\hbar = 2m = 1$.

Rewritten in this convenient units:

$i\frac{\partial}{\partial t} \Psi(\mathbf{r},t) = H\Psi(\mathbf{r},t)$ 

with $H$ as the Hamilton operator. 

Note: the cells in this notebook will run from top to bottom only, as the last two cells overwrite a few parameters used in the first.

In [1]:
import numpy as np
import scipy as sp
from scipy import sparse, linalg
from scipy.fftpack import fft, ifft
import scipy.sparse.linalg
import matplotlib.pyplot as plt
from matplotlib import animation

from JSAnimation.IPython_display import display_animation
from pylab import *
from mpl_toolkits.mplot3d import Axes3D

### Setting constants

In [2]:
dt = 0.005                      # time step 
t_max = 120                     # max time
N = 2 ** 11                     # number of bins over the x-axis (FFT works best with powers of two)
x_m = 100                       # x range over which the simulation runs
x = np.linspace(-x_m, x_m, N)   # computation points over the x-axis
dx = 2. * x_m / N               # step over the x-axis
dk = 2 * np.pi / (dx * N)       # step over the k-axis
k_m = -0.5 * N * dk             # lowest wave-number included in the simulation
k = k_m + dk * np.arange(N)     # bins in the k-space
V_x = np.zeros(N)               # array with potential values over the x-axis
V0 = 100                        # height of the barrier
width = 5                       # width of the barrier
p0 = 0.44                       # initial momentum
dp2 = p0 * p0 / 80.             # initial momentum dispersion
x0 = -0.5 * x_m                 # initial position of the wave-packet
d = 1 / np.sqrt(2 * dp2)        # wave-packet's width in the momentum-space
k0 = p0                         # particle's initial wave-number
v0 = p0                         # particle's initial velocity

# Plot parameters
xlimit = [x[0], x[-1]]
ylimit = [0, 1]

### Functions to make the wavefunctions and to set te various potentials

In [3]:
def gauss_x(x, a, x0, k0):
    """
    A gaussian wave packet of width a, centered at x0, with momentum k0.
    """
    return ((a * np.sqrt(np.pi)) ** (-0.5) * np.exp(-0.5 * ((x - x0) / a) ** 2 - 1j * x * k0))

def gauss_xy(X, Y, sigmax=1.0, sigmay=1.0, mux=0.0, muy=0.0, k0=0):
    """
    A two-dimensional gaussian wave packet, centered at (mux, muy), with momentum k0.
    """
    Xmu = X-mux
    Ymu = Y-muy

    z = Xmu**2/sigmax**2 + Ymu**2/sigmay**2
    psi = np.exp( -z/2 - 1j * X * k0)
    psi /= np.linalg.norm(psi)
    return np.reshape(psi, -1)

def plane_wave(x, k0=k0, x_zero = 3):
    """
    Creates a plane wave with momentum k0, and up to a point x_zero.
    """
    psi = np.exp(- 1j * x * k0)*(1/(np.exp(x/x_zero)+1))
    #psi[:,x_zero * N:N] = 0
    return np.reshape(psi, -1)

def gauss_k(k, a, x0, k0):
    """
    Analytical fourier transform of gauss_x, above.
    """
    return ((a / np.sqrt(np.pi)) ** 0.5 * np.exp(-0.5 * (a * (k - k0)) ** 2 - 1j * (k - k0) * x0))

def make_potential(V, width):
    """
    Step-wise potential which is zero everywhere except for a narrow region in the middle.
    """
    for a in range(len(V)): V[a] = 0
    for a in range(N/2-width,N/2+width): V[a] = V0

def make_2d_potential(V, height, width_V, Vx, width_slit, d):
    """
    Makes a potential barrier with two splits of width width_slit seperated by d.
    """
    V = np.zeros((N,N))
    Vy = int(N/2)
    d += width_slit
    V[:,Vx-width_V:Vx+width_V] = height
    V[Vy-width_slit+d:Vy+width_slit+d,:] = 0
    V[Vy-width_slit-d:Vy+width_slit-d,:] = 0
    return np.reshape(V,-1)


# Split-operator method

The dynamics of a one-dimensional quantum system are governed by the time-dependent Schrodinger equation

$i\frac{\partial}{\partial t} \Psi(x,t)
  = -\frac{\partial^2}{\partial x^2}\Psi + V \Psi$

We'll use a Fourier convention of the following form: 

$\widetilde{\Psi}(k, t) = \frac{1}{\sqrt{2\pi}}
  \int_{-\infty}^{\infty} \Psi(x, t) e^{-ikx} dx$

With the inverse Fourier transform of $\Psi$ as

$\Psi(x,t)=\frac{1}{\sqrt{2\pi}}\int_{-\infty}^{\infty}\tilde{\Psi}(k,t)e^{ikx}dk$

If we substitute this into the Schrödinger equation and simplifying we obtain

$i\frac{\partial }{\partial t} \widetilde{\Psi}(k,t)
  = k^2 \widetilde{\Psi}
  + iV\frac{\partial }{\partial k} \widetilde{\Psi}$

We now have two versions of the Schrödinger equation, both in $k$-space and in $x$-space.

The potential part of the Schrödinger equation in $x$-space

$i \frac{\partial}{\partial t} \Psi(x,t)=V(x)\Psi(x,t)$ 

is solved as follows:

$\Psi(x,t+\Delta t)=\Psi(x,t)e^{iV(x)\Delta t}$

Second, the straightforward part of the $k$-space Schrödinger equation

$i\frac{\partial}{\partial t} \widetilde{\Psi}
  = k^2 \widetilde{\Psi}$

is solved (for small $\Delta t$) as

$\tilde{\Psi}(k,t+\Delta t)=\tilde{\Psi}(k,t)e^{-ik^2\Delta t}$

So, we can solve both the potential part and the kinetic energy part can be solved by switching between $\Psi$ and $\tilde{\Psi}$ by using the Fast Fourier Transform (FFT).





### The algorithm

(1) Discretize $x$ and $k$-space by choosing $a$, $b$, $N$, $k_0$ as:

   $\Delta x = (b-a)/N,\;\; \Delta k = 2\pi/(b-a),\;\; k_0=-\pi/\Delta x, x_n=a+n\Delta x,\;\; k_m=k_0+m\Delta k$


(2) Discretize the wave-functions and potential:

   $\Psi_n(t):=\Psi(x_n,t),\;\; \tilde{\Psi}_m=\tilde{\Psi}(k_m,t),\;\; V_n:=V(x_n)$


(3) Evolve the system by one time step

   (3.1) Half step in $x$: $\Psi_n\leftarrow \Psi_n e^{-iV_n \Delta t/2}$
    
   (3.2) compute $\tilde{\Psi_m}$ from $\Psi_n$ using the FFT
    
   (3.3) Full step in $k$: $\tilde{\Psi}_m\leftarrow \tilde{\Psi}_m e^{-i k^2 \Delta t /2}$
    
   (3.4) Compute $\Psi_n$ from $\tilde{\Psi_m}$ using the Inverse FFT
    
   (3.5) The second half step in $x$: $\Psi_n\leftarrow \Psi_n e^{-iV_n \Delta t/2}$

(4) Repeat step (3) untill finished

### Initial conditions

We give the initial wavefunction the form of a gaussian wave packet of width $a$, centered at $x_0$, with momentum $k_0$:

$\Psi_n(x_0, t_0) = \frac{1}{\sqrt{a}\sqrt[4]{\pi}} e^{-\frac{(x-x_0)^2}{2a^2} - ixk_0}$

And the analytical fourier transform of $\Psi_n(x_0, t_0)$, above.

$\Psi_n(k_0, t_0) = \frac{\sqrt{a}}{\sqrt[4]{\pi}} e^{-a^2(k-k_0)^2/2 - ix_0(k-k_0)}$

The potential is of the form:

$V(x) = 
\begin{cases} 
 0 & \mbox{for } x < d,\; x>d  \\
\\
 V_0 & \mbox{for } -d \le x \le d
\end{cases}$

with a high potential at the borders to ensure full reflection.

Note: The same type of potential and wavefunction are used for the Crank-Nickelson method.


In [ ]:
# set up the potential and wavefunction
psi_x = gauss_x(x, d, x0, k0)    # particle's intitial wave-function
make_potential(V_x, width)       # set the potential over the x-range
V_x[x < -98] = 1E6               # high barrier at the borders
V_x[x > 98] = 1E6                # high barrier at the borders

# the time evolution steps
x_evolve_half = np.exp(-0.5 * 1j * dt * V_x ) # evolution operator in the x-space
k_evolve = np.exp(-0.5 * 1j * dt * k**2)      # evolution operator in the k-space

def step(t):
    """
    Peforms one time step of the algorithm described above.
    """
    global psi_x, psi_k
    psi_x *= x_evolve_half
    psi_k = fft(psi_x)
    psi_k *= k_evolve
    psi_x = ifft(psi_k)
    psi_x *= x_evolve_half
    
# functions for the animation
def init():
    psi_x_line.set_data([], [])
    V_x_line.set_data([], [])
    psi_x_line_im.set_data([], [])
    psi_x_line_re.set_data([], [])
    return psi_x_line, V_x_line, psi_x_line_im, psi_x_line_re,

def animate(t):
    step(t)
    psi_x_line.set_data(x, abs(psi_x))
    psi_x_line_im.set_data(x, psi_x.imag)
    psi_x_line_re.set_data(x, psi_x.real)
    V_x_line.set_data(x, V_x)
    return psi_x_line, V_x_line, psi_x_line_im, psi_x_line_re,

# plotting and animation
fig = plt.figure()
ax = plt.axes(xlim=(-x_m, x_m), ylim=(0, 1))
psi_x_line, = ax.plot([], [], c='r', label=r'$|\psi(x)|$')
psi_x_line_im, = ax.plot([], [], c='b', label=r'$\operatorname{Im}(\psi(x))$')
psi_x_line_re, = ax.plot([], [], c='g', label=r'$\operatorname{Re}(\psi(x))$')
V_x_line, = ax.plot([], [], c='k', label=r'$V(x)$')
title = ax.set_title("Split-Step Fourier method")
ax.legend(prop=dict(size=12))
ax.set_xlabel('$x$')
ax.set_ylabel(r'$|\psi(x)|$')

ani = animation.FuncAnimation(fig, animate, frames=100, interval=10, blit=True, init_func=init)

plt.show()

AttributeError: 'FigureCanvasMac' object has no attribute 'copy_from_bbox'

AttributeError: 'FigureCanvasMac' object has no attribute 'restore_region'

AttributeError: 'FigureCanvasMac' object has no attribute 'restore_region'

AttributeError: 'FigureCanvasMac' object has no attribute 'restore_region'

AttributeError: 'FigureCanvasMac' object has no attribute 'restore_region'

...

AttributeError: 'FigureCanvasMac' object has no attribute 'restore_region'

AttributeError: 'FigureCanvasMac' object has no attribute 'restore_region'

AttributeError: 'FigureCanvasMac' object has no attribute 'restore_region'

AttributeError: 'FigureCanvasMac' object has no attribute 'restore_region'

AttributeError: 'FigureCanvasMac' object has no attribute 'restore_region'

# Crank-Nicholson Algorithm

Continuing from $i\frac{\partial}{\partial t} \Psi(\mathbf{r},t) = H\Psi(\mathbf{r},t)$ 

Just as in the case of the Split-operator method, we first discretise $H$ at $L$ equidistant positions on the real axis, with separation $\Delta x$. The value of $\Psi$ at the point $x_k=j\Delta x$, $j=1,\dots,L$ is denoted by $\Psi_j$. 

Applying the Crank–Nicolson method to the Schodinger equation 

$\mathrm{i} \frac{\partial}{\partial t} \Psi = \left(-\frac{\partial^2}{\partial x^2} + V\right) \Psi$

results in 

$\left(I - \frac{\mathrm{i}\Delta t}{2(\Delta x)^2} H\right) \psi_{j+1} = \left(I + \frac{\mathrm{i}\Delta t}{2(\Delta x)^2} H\right) \psi_j$

We can write

$+\frac{\partial^2}{\partial x^2} \to A \equiv
\begin{pmatrix}
  -2 & 1       \\
  1  & -2 & 1  \\
     & 1  & -2 \\
     &    &    & \ddots
\end{pmatrix}.$

And use the biconjugate gradient stabilized method to solve for $\Psi_{j+1}$.

### One-dimensional problem with a gaussian wave packet

In [6]:
dt = 0.005
dx = 0.01

# set up the potential and wavefunction
psi_x = gauss_x(x, d, x0, k0)    # particle's intitial wave-function
make_potential(V_x, width)       # set the potential over the x-range
V_x[x < -98] = 1E6               # high barrier at the borders
V_x[x > 98] = 1E6                # high barrier at the borders

# Set up diagonal coefficients
A_diag = sp.empty(N, dtype=complex)
A_off_diag = sp.empty(N, dtype=complex)
B_diag = sp.empty(N, dtype=complex)
B_off_diag = sp.empty(N, dtype=complex)
A_diag.fill(1 - 1j * dt / (dx**2) )
A_off_diag.fill(1j * dt / (2 * dx**2) )
B_diag.fill(1 + 1j * dt / (dx**2) )
B_off_diag.fill(-1j * dt / (2 * dx**2) )

# Construct the sparse matrix
A = sp.sparse.spdiags([A_off_diag, A_diag, A_off_diag], [-1, 0, 1], N, N)
B = sp.sparse.spdiags([B_off_diag, B_diag, B_off_diag], [-1, 0, 1], N, N)

def step():
    global psi_x
    # Calculate effect of potential
    psi_x *= sp.exp(-1j * dt * V_x)

    # Calculate spacial derivatives with biconjugate gradient method
    psi_x = sp.sparse.linalg.bicgstab(A, B*psi_x)[0]

# functions for the animation
def init():
    psi_x_line.set_data([], [])
    V_x_line.set_data([], [])
    return psi_x_line, V_x_line,

def animate(t):
    step()
    psi_x_line.set_data(x, abs(psi_x))
    V_x_line.set_data(x, V_x)
    return psi_x_line, V_x_line,

# plotting and animation
fig = plt.figure()
ax = plt.axes(xlim=(xlimit), ylim=(ylimit))
psi_x_line, = ax.plot([], [], c='r', label=r'$|\psi(x)|$')
V_x_line, = ax.plot([], [], c='k', label=r'$V(x)$')
title = ax.set_title("Crank-Nicholson method")
ax.legend(prop=dict(size=12))
ax.set_xlabel('$x$')
ax.set_ylabel(r'$|\psi(x)|$')

ani = animation.FuncAnimation(fig, animate, frames=1500, interval=30, blit=True, init_func=init)

plt.show()

### Two-dimensional problem(s)

In [6]:
# This cell is just to print the table below.
from IPython.display import HTML
s = """
<table>
  <tr>
    <td>1<br>(1,1)</td>
    <td>2<br>(1,2)</td>
    <td>3<br>(1,3)</td>
    <td>4<br>(1,4)</td>
  </tr>
  <tr>
    <td>5<br>(2,1)</td>
    <td>6<br>(2,2)</td>
    <td>7<br>(2,3)</td>
    <td>8<br>(2,4)</td>
  </tr>
  <tr>
    <td>9<br>(3,1)</td>
    <td>10<br>(3,2)</td>
    <td>11<br>(3,3)</td>
    <td>12<br>(3,4)</td>
  </tr>
  <tr>
    <td>13<br>(4,1)</td>
    <td>14<br>(4,2)</td>
    <td>15<br>(4,3)</td>
    <td>16<br>(4,4)</td>
  </tr>
</table>"""

s2 = """
<table>
  <tr>
    <td>p<br>(j,k)</td>
  </tr>
</table>"""

print "A 4x4 lattice with its coordinates"
HTML(s)

A 4x4 lattice with its coordinates


In [7]:
print "in which the numbers mean"
HTML(s2)

in which the numbers mean


In two dimensions, we need to introduce a global ordering on the grid points and the unknowns.

$(j,k) \leftrightarrow p$

with 


$p = (k-1)n + j$

This is a common choice, and is called natural ordering by rows. Note that as $j$ and $k$ range from 1 through $n$, $p$ ranges from 1 through $N (= n^2)$. 
The relation between the $(j,k)$ indexing and the global $p$ indexing is depicted above for the $n = 4$ case.

At $(x_j,y_k)$ we use the finite difference approximation to the second derivative to replace the partial differential equation by the following difference equation

$f(x_j,y_k)=\frac{-U(j-1,k)+2 U(j,k)-U(j+1,k)-U(j,k-1)+2 U(j,k)-U(j,k+1)}{(\Delta x)^2}$


The two-dimensional Laplacian in matrix form (16 by 16) for the 4 by 4 grid above can be constructed as:

$ \nabla^2=
\begin{pmatrix}
-4 & 1 & 0 & 0 & 1 & 0 & 0\\
1 & -4 & 1 & 0 & 0 & 1 & 0\\
0 & 1 & -4 & 1 & 0 & 0 & 1\\
0 & 0 & 1 & -4 & 1 & 0 & 0\\
1 & 0 & 0 & 1 & -4 & 1 & 0\\
0 & 1 & 0 & 0 & 1 & -4 & 1\\
0 & 0 & 1 & 0 & 0 & 1 & \ddots
\end{pmatrix}
$

### The double slit experiment with a gaussian wave packet

Here a gaussian wave packet travels to the right and interferes with itself after the slits. 

The interference pattern is not as clearly visible as in the plainwave case described at the bottom of this notebook.

In [7]:
dt = 0.0002
dx = 0.01
N = 300


x = linspace(-x_m, x_m, N)
y = x
X,Y = meshgrid(x, y)
psi = gauss_xy(X, Y, sigmax=width, sigmay=width, mux=x0, muy=0, k0=k0)
V = np.zeros((N,N))
V = make_2d_potential(V, height=1e6, width_V=5, Vx=150, width_slit=5, d=20)
matshow(V.reshape(N,N))
plt.title('The potential shape')
plt.show()

# Set up diagonal coefficients
A_diag = sp.empty(N**2, dtype=complex)
A_off_diag = sp.empty(N**2, dtype=complex)
B_diag = sp.empty(N**2, dtype=complex)
B_off_diag = sp.empty(N**2, dtype=complex)
A_diag.fill(1 - 1j * 2 * dt / dx**2)
A_off_diag.fill(1j * dt / (2 * dx**2) )
B_diag.fill(1 + 1j * 2 * dt / dx**2)
B_off_diag.fill(-1j * dt/(2*dx**2))
A_off_diag[::N]=0; B_off_diag[::N]=0

# Construct the sparse matrix
A = sp.sparse.spdiags([A_off_diag, A_off_diag, A_diag, A_off_diag, A_off_diag], [-N, -1, 0, 1, N], N**2, N**2)
B = sp.sparse.spdiags([B_off_diag, B_off_diag, B_diag, B_off_diag, B_off_diag], [-N, -1, 0, 1, N], N**2, N**2)

def step():
    global psi
    # Calculate effect of potential
    psi *= sp.exp(-1j * dt * V)

    # Calculate spacial derivatives with biconjugate gradient method
    psi = sp.sparse.linalg.bicgstab(A, B*psi)[0]    
    
#fig = plt.figure()#ax = axes3d.Axes3D(fig)#plot = ax.plot_surface(X, Y, plot_psi)

fig, ax = plt.subplots()
plot_psi = np.reshape(psi.real, (N,N))
plot = ax.matshow(plot_psi)
title = ax.set_title("Crank-Nicholson method")
ax.set_xlabel(r'$x$')
ax.set_ylabel(r'$y$')

def update(i, ax, fig):
    step()
    plot_psi = np.reshape(abs(psi), (N,N))
    plot = ax.matshow(plot_psi)
    return plot,

ani = animation.FuncAnimation(fig, update, frames=1000, fargs=(ax, fig), interval=100)
plt.show()

### The double slit experiment with a plane wave packet

A plane wave is created on the whole lattice and then multiplied by a equation of the form of the Fermi-Dirac equation, such that the wave decays smoothly.

$\Psi(\mathbf{r},t=0) = e^{ik_0 x}/(e^{x/x_0}+1)$

One can observe the Huygens–Fresnel principle and easily see the interference pattern.

On the left and right boundary hard boundary conditions are used instead of periodic BC's, because it prevents the waves starting at the most left hand side from diffusing to the right hand side and interfere with the waves that traveled through the slits.

In [8]:
dt = 0.0005
dx = 0.01
N = 300

x = linspace(-x_m, x_m, N)
y = x
X,Y = meshgrid(x, y)
psi = plane_wave(X, k0=k0)
V = np.zeros((N,N))
V = make_2d_potential(V, height=1e6, width_V=10, Vx=150, width_slit=8, d=25)
matshow(V.reshape(N,N))
plt.title('The potential shape')
plt.show()

# Set up diagonal coefficients
A_diag = sp.empty(N**2, dtype=complex)
A_off_diag = sp.empty(N**2, dtype=complex)
B_diag = sp.empty(N**2, dtype=complex)
B_off_diag = sp.empty(N**2, dtype=complex)
A_diag.fill(1 - 1j * 2 * dt / dx**2)
A_off_diag.fill(1j * dt / (2 * dx**2) )
B_diag.fill(1 + 1j * 2 * dt / dx**2)
B_off_diag.fill(-1j * dt/(2*dx**2))
A_off_diag[::N]=0; B_off_diag[::N]=0

# Construct the sparse matrix
A = sp.sparse.spdiags([A_off_diag, A_off_diag, A_diag, A_off_diag, A_off_diag], [-N, -1, 0, 1, N], N**2, N**2)
B = sp.sparse.spdiags([B_off_diag, B_off_diag, B_diag, B_off_diag, B_off_diag], [-N, -1, 0, 1, N], N**2, N**2)

def step():
    global psi
    # Calculate effect of potential
    psi *= sp.exp(-1j * dt * V)

    # Calculate spacial derivatives with biconjugate gradient method
    psi = sp.sparse.linalg.bicgstab(A, B*psi)[0]    
    
fig, ax = plt.subplots()
plot_psi = np.reshape(psi, (N,N))
plot = ax.matshow(plot_psi.real)
title = ax.set_title("Crank-Nicholson method")
ax.set_xlabel(r'$x$')
ax.set_ylabel(r'$y$')

def update(i, ax, fig):
    step()
    plot_psi = np.reshape(psi, (N,N))
    vmax = abs(plot_psi[:,N/2:N]).max()
    plot = ax.matshow(plot_psi.real, vmax=vmax)
    return plot,

ani = animation.FuncAnimation(fig, update, frames=1000, fargs=(ax, fig), interval=100)
plt.show()